In [ ]:
##########################################################################################
#                                                                                        #
#  888888b.  8888888 .d88888b.   .d8888b.     .d8888b.   .d8888b.      d8888      d8888  #
#  888  "88b   888  d88P" "Y88b d88P  Y88b   d88P  Y88b d88P  Y88b    d8P888     d8P888  #
#  888  .88P   888  888     888 Y88b.        888        888          d8P 888    d8P 888  #
#  8888888K.   888  888     888  "Y888b.     888d888b.  888d888b.   d8P  888   d8P  888  #
#  888  "Y88b  888  888     888     "Y88b.   888P "Y88b 888P "Y88b d88   888  d88   888  #
#  888    888  888  888     888       "888   888    888 888    888 8888888888 8888888888 #
#  888   d88P  888  Y88b. .d88P Y88b  d88P   Y88b  d88P Y88b  d88P       888        888  #
#  8888888P" 8888888 "Y88888P"   "Y8888P"     "Y8888P"   "Y8888P"        888        888  #
#                                                                                        # 
##########################################################################################
#
# Wrangle CDC "Rare Diseases" data
#
##########################################################################################

In [18]:
##################################################################################################################
#
# YouDo:
#    1) Make a copy of this notebook with your name as a suffix:  
#       BIOS6644_XML_RareDiseases_FirstLast.ipynb
#    2) Do all work in this new notebook.
#    3) Submit completed work via GitHub pull request
#
##################################################################################################################


--2019-09-15 12:33:23--  https://data.cdc.gov/api/views/dwqk-w36f/rows.xml
Resolving data.cdc.gov (data.cdc.gov)... 52.206.68.26, 52.206.140.205, 52.206.140.199
Connecting to data.cdc.gov (data.cdc.gov)|52.206.68.26|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/xml]
Saving to: ‘rows.xml’

rows.xml                [         <=>        ]   2.29M  1007KB/s    in 2.3s    

2019-09-15 12:33:26 (1007 KB/s) - ‘rows.xml’ saved [2398754]



## Get Data data.gov

Data available at https://data.cdc.gov/api/views/45b4-9j7u/rows.xml



In [1]:
# Download with:
# Info: 
#     https://data.cdc.gov/NNDSS/NNDSS-Table-I-infrequently-reported-notifiable-dis/45b4-9j7u
#


#! wget https:\\data.cdc.gov\api\views\45b4-9j7u\rows.xml
#! mv rows.xml Data/

## Instructor comment
## Windows file structures use backwards slashes.  URLs don't :)

In [9]:
import numpy as np
import pandas as pd
import pylab as plt
%matplotlib notebook

#import xml.etree.ElementTree as ET
from lxml import etree as ET

In [10]:
# Adapted from:  https://python-forum.io/Thread-How-to-display-XML-tree-structure-with-Python

def xml_tree_vis(filename):
    import re, collections
    from lxml import etree as ET

    raw_tree = ET.parse(filename)
    xml_root = raw_tree.getroot()      # the top-most node
    nice_tree = collections.OrderedDict()

    for tag in xml_root.iter():
        path = re.sub('\[[0-9]+\]', '', raw_tree.getpath(tag))
        if path not in nice_tree:
            nice_tree[path] = []
        if len(tag.keys()) > 0:
            nice_tree[path].extend(attrib for attrib in tag.keys() if attrib not in nice_tree[path])            

    for path, attribs in nice_tree.items():
        indent = int(path.count('/') - 1)
        nodename = path.split('/')[-1]
        if len(attribs) > 0:
            attribslist =  ', '.join(attribs)  
        else:
            attribslist = '-'
            
        print('{0}{1}: {2} [{3}]'.format('    ' * indent, indent, nodename, attribslist))
        
# Visualize this file's structure
xml_tree_vis('../Data/rows.xml')

0: response [-]
    1: row [-]
        2: row [_id, _uuid, _position, _address]
            3: disease [-]
            3: mmwr_year [-]
            3: mmwr_week [-]
            3: current_week_flag [-]
            3: cum_2017_flag [-]
            3: _5_year_weekly_average_flag [-]
            3: total_cases_reported_2016_flag [-]
            3: total_cases_reported_2015_flag [-]
            3: total_cases_reported_2014_flag [-]
            3: total_cases_reported_2013_flag [-]
            3: total_cases_reported_2012_flag [-]
            3: _5_year_weekly_average [-]
            3: total_cases_reported_2016 [-]
            3: total_cases_reported_2015 [-]
            3: total_cases_reported_2014 [-]
            3: total_cases_reported_2013 [-]
            3: total_cases_reported_2012 [-]
            3: current_week [-]
            3: cum_2017 [-]
            3: states_reporting_cases_during_current_week_no [-]


In [13]:
# Notice there are two levels with the tag "row"  This sort of thing is common in 
# XML and really annoying.  
# This sort of display makes it stand out, though.
# We'll need to remember that for later.

In [12]:

#  Read the entire tree into a collection of "nodes"
#  each of which have several associated attributes,
#  possibly including other "child nodes"
#
#  Web browsers can display XML in a relatively
#  easy-to-read way.  Open rows.xml with your browser.

# Open the file in Python: 
tree = ET.parse('../Data/rows.xml')
root = tree.getroot()      # the top-most node


In [13]:
tree

In [14]:
root

<Element response at 0x11a4a5e08>

In [22]:
# This data seems to be organized by an attribute called "row", each of 
#  which has several children (probably the columns)

In [15]:
# You can see root's child nodes with

for xx in root.iter():
    print(xx)

# This shows all of the children of root, without regard to their position in the tree.
# In this data set, though, we want to parse each row separately.


<Element response at 0x11a4a5e08>
<Element row at 0x119e7bd08>
<Element row at 0x11b130a88>
<Element disease at 0x11a405048>
<Element mmwr_year at 0x119e7bd08>
<Element mmwr_week at 0x11b130a88>
<Element current_week_flag at 0x11b15bc08>
<Element cum_2017_flag at 0x11a405048>
<Element _5_year_weekly_average_flag at 0x11b130a88>
<Element total_cases_reported_2016_flag at 0x119e7bd08>
<Element total_cases_reported_2015_flag at 0x11a405048>
<Element total_cases_reported_2014_flag at 0x11b130a88>
<Element total_cases_reported_2013_flag at 0x119e7bd08>
<Element total_cases_reported_2012_flag at 0x11a405048>
<Element row at 0x11b130a88>
<Element disease at 0x119e7bd08>
<Element mmwr_year at 0x11a405048>
<Element mmwr_week at 0x11b130a88>
<Element current_week_flag at 0x11b15bc08>
<Element cum_2017_flag at 0x119e7bd08>
<Element _5_year_weekly_average at 0x11b130a88>
<Element total_cases_reported_2016 at 0x11a405048>
<Element total_cases_reported_2015 at 0x119e7bd08>
<Element total_cases_repor

<Element total_cases_reported_2012 at 0x11a475248>
<Element row at 0x11a4752c8>
<Element disease at 0x11a407ac8>
<Element mmwr_year at 0x11a475248>
<Element mmwr_week at 0x11a4752c8>
<Element current_week at 0x11a407908>
<Element cum_2017 at 0x11a407ac8>
<Element _5_year_weekly_average at 0x11a475248>
<Element total_cases_reported_2016 at 0x11a407908>
<Element total_cases_reported_2015 at 0x11a4752c8>
<Element total_cases_reported_2014 at 0x11a475248>
<Element total_cases_reported_2013 at 0x11a407908>
<Element total_cases_reported_2012 at 0x11a4752c8>
<Element states_reporting_cases_during_current_week_no at 0x11a475248>
<Element row at 0x11a407908>
<Element disease at 0x11a4752c8>
<Element mmwr_year at 0x11a475248>
<Element mmwr_week at 0x11a407908>
<Element current_week_flag at 0x11a407ac8>
<Element cum_2017_flag at 0x11a4752c8>
<Element _5_year_weekly_average_flag at 0x11a475248>
<Element total_cases_reported_2016_flag at 0x11a407908>
<Element total_cases_reported_2015_flag at 0x11a

<Element mmwr_year at 0x11a475248>
<Element mmwr_week at 0x11a475308>
<Element current_week_flag at 0x11a407908>
<Element cum_2017_flag at 0x11a4074c8>
<Element _5_year_weekly_average_flag at 0x11a475308>
<Element total_cases_reported_2016 at 0x11a407908>
<Element total_cases_reported_2015 at 0x11a475248>
<Element total_cases_reported_2014 at 0x11a475308>
<Element total_cases_reported_2013 at 0x11a407908>
<Element total_cases_reported_2012 at 0x11a475248>
<Element row at 0x11a475308>
<Element disease at 0x11a407908>
<Element mmwr_year at 0x11a475248>
<Element mmwr_week at 0x11a475308>
<Element current_week at 0x11a4074c8>
<Element cum_2017 at 0x11a407908>
<Element _5_year_weekly_average at 0x11a475248>
<Element total_cases_reported_2016 at 0x11a4074c8>
<Element total_cases_reported_2015 at 0x11a475308>
<Element total_cases_reported_2014 at 0x11a475248>
<Element total_cases_reported_2013 at 0x11a4074c8>
<Element total_cases_reported_2012 at 0x11a475308>
<Element states_reporting_cases_d

<Element total_cases_reported_2015 at 0x11a40cdc8>
<Element total_cases_reported_2014 at 0x11a4752c8>
<Element total_cases_reported_2013 at 0x11a40ccc8>
<Element total_cases_reported_2012 at 0x11a40cdc8>
<Element row at 0x11a4752c8>
<Element disease at 0x11a40ccc8>
<Element mmwr_year at 0x11a40cdc8>
<Element mmwr_week at 0x11a4752c8>
<Element current_week_flag at 0x11a40c6c8>
<Element cum_2017_flag at 0x11a40ccc8>
<Element _5_year_weekly_average_flag at 0x11a4752c8>
<Element total_cases_reported_2016_flag at 0x11a40cdc8>
<Element total_cases_reported_2015_flag at 0x11a40ccc8>
<Element total_cases_reported_2014 at 0x11a4752c8>
<Element total_cases_reported_2013_flag at 0x11a40cdc8>
<Element total_cases_reported_2012 at 0x11a40ccc8>
<Element row at 0x11a4752c8>
<Element disease at 0x11a40cdc8>
<Element mmwr_year at 0x11a40ccc8>
<Element mmwr_week at 0x11a4752c8>
<Element current_week_flag at 0x11a40c6c8>
<Element cum_2017_flag at 0x11a40cdc8>
<Element _5_year_weekly_average_flag at 0x11a

<Element disease at 0x11a40c6c8>
<Element mmwr_year at 0x11a40ccc8>
<Element mmwr_week at 0x11a40cec8>
<Element current_week_flag at 0x11a40c9c8>
<Element cum_2017_flag at 0x11a40c6c8>
<Element _5_year_weekly_average at 0x11a40cec8>
<Element total_cases_reported_2016_flag at 0x11a40ccc8>
<Element total_cases_reported_2015_flag at 0x11a40c6c8>
<Element total_cases_reported_2014 at 0x11a40cec8>
<Element total_cases_reported_2013_flag at 0x11a40ccc8>
<Element total_cases_reported_2012 at 0x11a40c6c8>
<Element row at 0x11a40cec8>
<Element disease at 0x11a40ccc8>
<Element mmwr_year at 0x11a40c6c8>
<Element mmwr_week at 0x11a40cec8>
<Element current_week_flag at 0x11a40c9c8>
<Element cum_2017 at 0x11a40ccc8>
<Element _5_year_weekly_average at 0x11a40cec8>
<Element total_cases_reported_2016 at 0x11a40c6c8>
<Element total_cases_reported_2015 at 0x11a40ccc8>
<Element total_cases_reported_2014 at 0x11a40cec8>
<Element total_cases_reported_2013 at 0x11a40c6c8>
<Element total_cases_reported_2012 a

...

<Element total_cases_reported_2012 at 0x11a478e48>
<Element row at 0x11a478e08>
<Element disease at 0x11a40cec8>
<Element mmwr_year at 0x11a478e48>
<Element mmwr_week at 0x11a478e08>
<Element current_week_flag at 0x11a478b08>
<Element cum_2017_flag at 0x11a478e48>
<Element _5_year_weekly_average_flag at 0x11a40cec8>
<Element total_cases_reported_2016_flag at 0x11a478e08>
<Element total_cases_reported_2015_flag at 0x11a478e48>
<Element total_cases_reported_2014_flag at 0x11a40cec8>
<Element total_cases_reported_2013_flag at 0x11a478e08>
<Element total_cases_reported_2012_flag at 0x11a478e48>
<Element row at 0x11a40cec8>
<Element disease at 0x11a478e08>
<Element mmwr_year at 0x11a478e48>
<Element mmwr_week at 0x11a40cec8>
<Element current_week at 0x11a478b08>
<Element cum_2017 at 0x11a478e08>
<Element _5_year_weekly_average at 0x11a478e48>
<Element total_cases_reported_2016 at 0x11a478b08>
<Element total_cases_reported_2015 at 0x11a40cec8>
<Element total_cases_reported_2014 at 0x11a478e4

<Element _5_year_weekly_average_flag at 0x11a40cec8>
<Element total_cases_reported_2016_flag at 0x11a478bc8>
<Element total_cases_reported_2015_flag at 0x11a478e48>
<Element total_cases_reported_2014_flag at 0x11a40cec8>
<Element total_cases_reported_2013_flag at 0x11a478bc8>
<Element total_cases_reported_2012_flag at 0x11a478e48>
<Element row at 0x11a40cec8>
<Element disease at 0x11a478bc8>
<Element mmwr_year at 0x11a478e48>
<Element mmwr_week at 0x11a40cec8>
<Element current_week at 0x11a478b08>
<Element cum_2017 at 0x11a478bc8>
<Element _5_year_weekly_average at 0x11a478e48>
<Element total_cases_reported_2016 at 0x11a478b08>
<Element total_cases_reported_2015 at 0x11a40cec8>
<Element total_cases_reported_2014 at 0x11a478e48>
<Element total_cases_reported_2013 at 0x11a478b08>
<Element total_cases_reported_2012 at 0x11a40cec8>
<Element states_reporting_cases_during_current_week_no at 0x11a478e48>
<Element row at 0x11a478b08>
<Element disease at 0x11a40cec8>
<Element mmwr_year at 0x11a

<Element mmwr_year at 0x11a478e48>
<Element mmwr_week at 0x11a40cec8>
<Element current_week_flag at 0x11a478e08>
<Element cum_2017_flag at 0x11a478bc8>
<Element _5_year_weekly_average_flag at 0x11a40cec8>
<Element total_cases_reported_2016_flag at 0x11a478e48>
<Element total_cases_reported_2015_flag at 0x11a478bc8>
<Element total_cases_reported_2014_flag at 0x11a40cec8>
<Element total_cases_reported_2013_flag at 0x11a478e48>
<Element total_cases_reported_2012_flag at 0x11a478bc8>
<Element row at 0x11a40cec8>
<Element disease at 0x11a478e48>
<Element mmwr_year at 0x11a478bc8>
<Element mmwr_week at 0x11a40cec8>
<Element current_week_flag at 0x11a478e08>
<Element cum_2017_flag at 0x11a478e48>
<Element _5_year_weekly_average_flag at 0x11a40cec8>
<Element total_cases_reported_2016_flag at 0x11a478bc8>
<Element total_cases_reported_2015_flag at 0x11a478e48>
<Element total_cases_reported_2014_flag at 0x11a40cec8>
<Element total_cases_reported_2013_flag at 0x11a478bc8>
<Element total_cases_rep

<Element total_cases_reported_2012 at 0x11a478ec8>
<Element row at 0x11a478b88>
<Element disease at 0x11a478b08>
<Element mmwr_year at 0x11a478ec8>
<Element mmwr_week at 0x11a478b88>
<Element current_week_flag at 0x11a478bc8>
<Element cum_2017 at 0x11a478b08>
<Element _5_year_weekly_average at 0x11a478b88>
<Element total_cases_reported_2016 at 0x11a478ec8>
<Element total_cases_reported_2015 at 0x11a478b08>
<Element total_cases_reported_2014 at 0x11a478b88>
<Element total_cases_reported_2013 at 0x11a478ec8>
<Element total_cases_reported_2012 at 0x11a478b08>
<Element row at 0x11a478b88>
<Element disease at 0x11a478ec8>
<Element mmwr_year at 0x11a478b08>
<Element mmwr_week at 0x11a478b88>
<Element current_week_flag at 0x11a478bc8>
<Element cum_2017 at 0x11a478ec8>
<Element _5_year_weekly_average at 0x11a478b88>
<Element total_cases_reported_2016 at 0x11a478b08>
<Element total_cases_reported_2015 at 0x11a478ec8>
<Element total_cases_reported_2014 at 0x11a478b88>
<Element total_cases_report

<Element cum_2017 at 0x11a478b08>
<Element _5_year_weekly_average at 0x11a478b88>
<Element total_cases_reported_2016 at 0x11a478e08>
<Element total_cases_reported_2015 at 0x11a478b08>
<Element total_cases_reported_2014 at 0x11a478b88>
<Element total_cases_reported_2013 at 0x11a478e08>
<Element total_cases_reported_2012 at 0x11a478b08>
<Element row at 0x11a478b88>
<Element disease at 0x11a478e08>
<Element mmwr_year at 0x11a478b08>
<Element mmwr_week at 0x11a478b88>
<Element current_week_flag at 0x11a478e48>
<Element cum_2017 at 0x11a478e08>
<Element _5_year_weekly_average at 0x11a478b88>
<Element total_cases_reported_2016 at 0x11a478b08>
<Element total_cases_reported_2015_flag at 0x11a478e08>
<Element total_cases_reported_2014_flag at 0x11a478b88>
<Element total_cases_reported_2013_flag at 0x11a478b08>
<Element total_cases_reported_2012_flag at 0x11a478e08>
<Element row at 0x11a478b88>
<Element disease at 0x11a478b08>
<Element mmwr_year at 0x11a478e08>
<Element mmwr_week at 0x11a478b88>

In [16]:
## Here's how you iterate through only the nodes called "row"
for xx in root.iter('row'):
    print(xx)


<Element row at 0x1097e4f88>
<Element row at 0x11a478448>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x11a478448>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x11a478448>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x11a478448>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x11a478448>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x11a478448>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x11a478448>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x11a478448>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x11a478448>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x11a478448>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x11a478448>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row a

<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x10974e348>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x10974e348>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x10974e348>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x10974e348>
<Element row at 0x11b21c1c8>
<Element row at 0x1097e4f88>
<Element row at 0x10974e348>
<Element row at 0x11b21c1c8>


In [19]:
len(root)

1

In [17]:
##################################################################################################################
#
# YouDo:
#
#   You'd like to generate a list of all the diseases on this list.  There are several ways to do this,
#   but unlike the "row" nodes, the data seems to consistently use the element name "disease".
#
#   1) Generate a list of all nodes called "disease" 
#
#######################################  BEGIN STUDENT CODE  #####################################################

diseases = list(root.iter('disease'))


In [18]:
for xx in root.iter('disease'):
    print(xx)

<Element disease at 0x11a478bc8>
<Element disease at 0x11a478508>
<Element disease at 0x11a4780c8>
<Element disease at 0x11a4786c8>
<Element disease at 0x11a478548>
<Element disease at 0x11a478788>
<Element disease at 0x11a478248>
<Element disease at 0x11a478188>
<Element disease at 0x11a478148>
<Element disease at 0x11a478708>
<Element disease at 0x11a478848>
<Element disease at 0x11a4782c8>
<Element disease at 0x11a478888>
<Element disease at 0x11a4783c8>
<Element disease at 0x11a478208>
<Element disease at 0x11a4788c8>
<Element disease at 0x11a478948>
<Element disease at 0x11a478908>
<Element disease at 0x11a478488>
<Element disease at 0x11a478308>
<Element disease at 0x11a478388>
<Element disease at 0x11a478588>
<Element disease at 0x11a478408>
<Element disease at 0x11b03dd48>
<Element disease at 0x11b03dcc8>
<Element disease at 0x11b03da88>
<Element disease at 0x11b03dc48>
<Element disease at 0x11b03dc88>
<Element disease at 0x11b03da08>
<Element disease at 0x11b03d908>
<Element d

<Element disease at 0x11b28ac88>
<Element disease at 0x11b28acc8>
<Element disease at 0x11b28ad08>
<Element disease at 0x11b28ad48>
<Element disease at 0x11b28ad88>
<Element disease at 0x11b28adc8>
<Element disease at 0x11b28ae08>
<Element disease at 0x11b28ae48>
<Element disease at 0x11b28ae88>
<Element disease at 0x11b28aec8>
<Element disease at 0x11b28af08>
<Element disease at 0x11b28af48>
<Element disease at 0x11b28af88>
<Element disease at 0x11b28afc8>
<Element disease at 0x11b289048>
<Element disease at 0x11b289088>
<Element disease at 0x11b2890c8>
<Element disease at 0x11b289108>
<Element disease at 0x11b289148>
<Element disease at 0x11b289188>
<Element disease at 0x11b2891c8>
<Element disease at 0x11b289208>
<Element disease at 0x11b289248>
<Element disease at 0x11b289288>
<Element disease at 0x11b2892c8>
<Element disease at 0x11b289308>
<Element disease at 0x11b289348>
<Element disease at 0x11b289388>
<Element disease at 0x11b2893c8>
<Element disease at 0x11b289408>
<Element d

In [19]:
diseases = list(root.iter('disease'))

In [20]:
len(diseases)

3329

In [21]:
diseases[0]

<Element disease at 0x11a478bc8>

In [ ]:
#######################################   END STUDENT CODE   #####################################################

In [22]:
# These nodes have various attributes which you can view like this:
dir(diseases[0])


['__bool__',
 '__class__',
 '__contains__',
 '__copy__',
 '__deepcopy__',
 '__delattr__',
 '__delitem__',
 '__dir__',
 '__doc__',
 '__eq__',
 '__format__',
 '__ge__',
 '__getattribute__',
 '__getitem__',
 '__gt__',
 '__hash__',
 '__init__',
 '__init_subclass__',
 '__iter__',
 '__le__',
 '__len__',
 '__lt__',
 '__ne__',
 '__new__',
 '__reduce__',
 '__reduce_ex__',
 '__repr__',
 '__reversed__',
 '__setattr__',
 '__setitem__',
 '__sizeof__',
 '__str__',
 '__subclasshook__',
 '_init',
 'addnext',
 'addprevious',
 'append',
 'attrib',
 'base',
 'clear',
 'cssselect',
 'extend',
 'find',
 'findall',
 'findtext',
 'get',
 'getchildren',
 'getiterator',
 'getnext',
 'getparent',
 'getprevious',
 'getroottree',
 'index',
 'insert',
 'items',
 'iter',
 'iterancestors',
 'iterchildren',
 'iterdescendants',
 'iterfind',
 'itersiblings',
 'itertext',
 'keys',
 'makeelement',
 'nsmap',
 'prefix',
 'remove',
 'replace',
 'set',
 'sourceline',
 'tag',
 'tail',
 'text',
 'values',
 'xpath']

In [23]:
# One of the key attribtues is the "text" attribute which contains the
# disease names we're looking for.
#
diseases[0].text

'Anthrax'

In [24]:
diseases[1].text

'Arboviral diseases¶,** Chikungunya virus disease'

In [25]:
diseases[0].values

<bound method _Element.values of <Element disease at 0x11a478bc8>>

In [26]:


##################################################################################################################
#
# YouDo:
#
# 1) Loop through the list of nodes and extract the text attribute of each node into a list called diz
#    
#   Stretch goal:  do this with a list comprehension
#
# 2) Make a second list called udiz containing only the unique members of this data set 

#######################################  BEGIN STUDENT CODE  #####################################################
# 1)
diz = [node.text for node in diseases]
diz


['Anthrax',
 'Arboviral diseases¶,** Chikungunya virus disease',
 'Arboviral diseases¶,** Eastern equine encephalitis virus disease',
 'Arboviral diseases¶,** Jamestown Canyon virus disease',
 'Arboviral diseases¶,** La Crosse virus disease',
 'Arboviral diseases¶,** Powassan virus disease',
 'Arboviral diseases¶,** St. Louis encephalitis virus disease',
 'Arboviral diseases¶,** Western equine encephalitis virus disease',
 'Botulism, total',
 'Botulism, foodborne',
 'Botulism, infant',
 'Botulism, other (wound and unspecified)',
 'Brucellosis',
 'Chancroid',
 'Cholera',
 'Cyclosporiasis**',
 'Diphtheria',
 'Haemophilus influenzae invasive disease (age <5 yrs)††, serotype b',
 'Haemophilus influenzae invasive disease (age <5 yrs)††, nontypeable ',
 'Haemophilus influenzae invasive disease (age <5 yrs)††, non-b serotype',
 'Haemophilus influenzae invasive disease (age <5 yrs)††, unknown serotype',
 "Hansen's disease**",
 'Hantavirus**, Hantavirus infection, non-HPS',
 'Hantavirus**, Hant

In [46]:
#2)
udiz = sorted(list(set(diz)))
udiz

['Anthrax',
 'Arboviral diseases¶,** Chikungunya virus disease',
 'Arboviral diseases¶,** Chikungunya virus††',
 'Arboviral diseases¶,** Eastern equine encephalitis virus ',
 'Arboviral diseases¶,** Eastern equine encephalitis virus disease',
 'Arboviral diseases¶,** Jamestown Canyon virus disease',
 'Arboviral diseases¶,** Jamestown Canyon virus§§ ',
 'Arboviral diseases¶,** La Crosse virus disease',
 'Arboviral diseases¶,** La Crosse virus§§ ',
 'Arboviral diseases¶,** Powassan virus ',
 'Arboviral diseases¶,** Powassan virus disease',
 'Arboviral diseases¶,** St. Louis encephalitis virus ',
 'Arboviral diseases¶,** St. Louis encephalitis virus disease',
 'Arboviral diseases¶,** Western equine encephalitis virus ',
 'Arboviral diseases¶,** Western equine encephalitis virus disease',
 'Botulism, foodborne',
 'Botulism, infant',
 'Botulism, other (wound and unspecified)',
 'Botulism, total',
 'Brucellosis',
 'Chancroid',
 'Cholera',
 'Cyclosporiasis**',
 'Diphtheria',
 'Haemophilus inf

In [44]:
#######################################   END STUDENT CODE   #####################################################

In [27]:

# This data set uses a column called cum_2017 to report the cumulative number of reports of that disease
# in 2017
##################################################################################################################
#
# YouDo:
# Generate a list of the top 5 most reported of these diseases in 2017 and the number of reports of each
#
# Note: This is a pain without using Pandas.   Give it a go and see how far you get in 30 minutes.
#       After that, feel free to abandon it and use Pandas in the cell below.
#
#######################################  BEGIN STUDENT CODE  #####################################################

# Make an empty dictionary 
disease_reports = dict()

#(diseases[20].getparent()).find('cum_2017').text
#(diseases[20].getparent()).find('disease').text

for dis in diseases:
    # Find the parent node of each disease node
    parent = dis.getparent()
    # Find the disease name of the parent node
    this_disease = parent.find('disease').text
    # Find the cum_2017 node of the parent node
    this_cum = parent.find('cum_2017')
    
    if this_cum == None:
        this_total_cum = 0
    else:
        this_total_cum = int(this_cum.text)
    
    # The dictionary will have disease as keys and number of incidents as values
    
    if this_disease not in disease_reports.keys():
        disease_reports.update({this_disease: this_total_cum})
    else:
        cum = disease_reports[this_disease]
        cum = cum + this_total_cum
        disease_reports[this_disease] = cum
   

# sort the dictionary by incidents
disease_reports_sort = sorted(disease_reports.items() ,  key=lambda x: x[1], reverse = True)
disease_reports_sort[0:5]    

#######################################   END STUDENT CODE   ####################################################

[('Cyclosporiasis**', 22181),
 ('Listeriosis', 16201),
 ('Syphilis, congenital¶¶¶', 12316),
 ('Zika virus disease, non-congenital††††  ', 11349),
 ('Streptococcal toxic-shock syndrome**', 7889)]

In [138]:
##################################################################################################################
#
# YouDo:  If you abandoned hope above, try reading the reports dictionary into a data frame, try importing
# reports into a data frame and sorting it.

#######################################  BEGIN STUDENT CODE  #####################################################

df = pd.DataFrame([disease_reports.keys(), disease_reports.values()]).T
df.columns=['Disease','Counts']
df.sort_values('Counts',ascending=False,inplace=True)
df.iloc[:5,:]



#######################################   END STUDENT CODE   #####################################################

Disease Counts
15                          Cyclosporiasis**  22181
28                               Listeriosis  16201
46                   Syphilis, congenital¶¶¶  12316
63  Zika virus disease, non-congenital††††    11349
45      Streptococcal toxic-shock syndrome**   7889

# The Pandas Way

In [148]:
import sys
!conda install --yes --prefix {sys.prefix} xmltodict

Solving environment: ...working... done

## Package Plan ##

  environment location: C:\Users\emily\Anaconda3

  added / updated specs:
    - xmltodict


The following packages will be downloaded:

    package                    |            build
    ---------------------------|-----------------
    conda-4.7.12               |           py37_0         3.0 MB
    xmltodict-0.12.0           |             py_0          14 KB
    ------------------------------------------------------------
                                           Total:         3.0 MB

The following NEW packages will be INSTALLED:

  xmltodict          pkgs/main/noarch::xmltodict-0.12.0-py_0

The following packages will be UPDATED:

  conda                                       4.7.10-py37_0 --> 4.7.12-py37_0




conda-4.7.12         | 3.0 MB    |            |   0% 
conda-4.7.12         | 3.0 MB    |            |   1% 
conda-4.7.12         | 3.0 MB    | #9         |  19% 
conda-4.7.12         | 3.0 MB    | ####2      |

In [29]:
import xml.etree.ElementTree as ET
import xmltodict
import json

tree = ET.parse('../Data/rows.xml')
xml_data = tree.getroot()

xmlstr = ET.tostring(xml_data, encoding='ascii', method='xml')


data_dict = dict(xmltodict.parse(xmlstr))

print(data_dict.keys())



dict_keys(['response'])


In [30]:
data_dict

{'response': OrderedDict([('row',
               OrderedDict([('row',
                             [OrderedDict([('@_address',
                                            'https://data.cdc.gov/resource/_45b4-9j7u/row-skhd-7gcj-bknc'),
                                           ('@_id', 'row-skhd-7gcj-bknc'),
                                           ('@_position', '0'),
                                           ('@_uuid',
                                            '00000000-0000-0000-8068-71B30911A10A'),
                                           ('disease', 'Anthrax'),
                                           ('mmwr_year', '2017'),
                                           ('mmwr_week', '1'),
                                           ('current_week_flag', '-'),
                                           ('cum_2017_flag', '-'),
                                           ('_5_year_weekly_average_flag',
                                            '-'),
                            

In [31]:
# Data Dict will reflect the structure 
#  The visualization helps
# Notice that the first of dict_keys is "response"
# which is the same as the "root" of the xml tree
#
xml_tree_vis('../Data/rows.xml')


0: response [-]
    1: row [-]
        2: row [_id, _uuid, _position, _address]
            3: disease [-]
            3: mmwr_year [-]
            3: mmwr_week [-]
            3: current_week_flag [-]
            3: cum_2017_flag [-]
            3: _5_year_weekly_average_flag [-]
            3: total_cases_reported_2016_flag [-]
            3: total_cases_reported_2015_flag [-]
            3: total_cases_reported_2014_flag [-]
            3: total_cases_reported_2013_flag [-]
            3: total_cases_reported_2012_flag [-]
            3: _5_year_weekly_average [-]
            3: total_cases_reported_2016 [-]
            3: total_cases_reported_2015 [-]
            3: total_cases_reported_2014 [-]
            3: total_cases_reported_2013 [-]
            3: total_cases_reported_2012 [-]
            3: current_week [-]
            3: cum_2017 [-]
            3: states_reporting_cases_during_current_week_no [-]


In [156]:
# We need to get down to the second level of "row"
#
##################################################################################################################
#
# YouDo: 
# Uncomment the following and look at them in turn
#print(data_dict['response'])
#print(data_dict['response']['row'])
print(data_dict['response']['row']['row'])

[OrderedDict([('@_address', 'https://data.cdc.gov/resource/_45b4-9j7u/row-skhd-7gcj-bknc'), ('@_id', 'row-skhd-7gcj-bknc'), ('@_position', '0'), ('@_uuid', '00000000-0000-0000-8068-71B30911A10A'), ('disease', 'Anthrax'), ('mmwr_year', '2017'), ('mmwr_week', '1'), ('current_week_flag', '-'), ('cum_2017_flag', '-'), ('_5_year_weekly_average_flag', '-'), ('total_cases_reported_2016_flag', '-'), ('total_cases_reported_2015_flag', '-'), ('total_cases_reported_2014_flag', '-'), ('total_cases_reported_2013_flag', '-'), ('total_cases_reported_2012_flag', '-')]), OrderedDict([('@_address', 'https://data.cdc.gov/resource/_45b4-9j7u/row-vyec_dmte-gwmz'), ('@_id', 'row-vyec_dmte-gwmz'), ('@_position', '0'), ('@_uuid', '00000000-0000-0000-F7D9-05250D543B3D'), ('disease', 'Arboviral diseases¶,** Chikungunya virus disease'), ('mmwr_year', '2017'), ('mmwr_week', '1'), ('current_week_flag', '-'), ('cum_2017_flag', '-'), ('_5_year_weekly_average', '6'), ('total_cases_reported_2016', '167'), ('total_case

In [32]:
# Once we get to here:
#    data_dict['response']['row']['row']
# We start to get data that looks like actual rows.
# We can make a data frame from this:
df2 = pd.DataFrame(data_dict['response']['row']['row'])

In [33]:
df2

@_address                @_id  \
0     https://data.cdc.gov/resource/_45b4-9j7u/row-s...  row-skhd-7gcj-bknc   
1     https://data.cdc.gov/resource/_45b4-9j7u/row-v...  row-vyec_dmte-gwmz   
2     https://data.cdc.gov/resource/_45b4-9j7u/row-h...  row-hdxc_43ap~n6yz   
3     https://data.cdc.gov/resource/_45b4-9j7u/row-t...  row-t9wt_thhz_94py   
4     https://data.cdc.gov/resource/_45b4-9j7u/row-b...  row-bkgt~e7aa.8vhi   
5     https://data.cdc.gov/resource/_45b4-9j7u/row-s...  row-sztx_txbm~vsg3   
6     https://data.cdc.gov/resource/_45b4-9j7u/row-6...  row-6khc.wagz.utpy   
7     https://data.cdc.gov/resource/_45b4-9j7u/row-m...  row-m6tc.gzn9-t86m   
8     https://data.cdc.gov/resource/_45b4-9j7u/row-j...  row-jvcs.f8as_zyzq   
9     https://data.cdc.gov/resource/_45b4-9j7u/row-x...  row-xt2k~2xxr_tuwm   
10    https://data.cdc.gov/resource/_45b4-9j7u/row-n...  row-nf2e-8fif_cfac   
11    https://data.cdc.gov/resource/_45b4-9j7u/row-q...  row-qdbs~rqa6-ruar   
12    https://data.cdc.gov/resource/_45b4-9j7u/row-p...  row-pzph_v3tt_g3rg   
13    https://data.cdc.gov/resource/_45b4-9j7u/row-m...  row-mhbe~v89c.cnjk   
14    https://data.cdc.gov/resource/_45b4-9j7u/row-3...  row-3wbu.ndx2-r8q5   
15    https://data.cdc.gov/resource/_45b4-9j7u/row-v...  row-vn9y~6t3a~xv9z   
16    https://data.cdc.gov/resource/_45b4-9j7u/row-c...  row-cd6y.cxzv_tcih   
17    https://data.cdc.gov/resource/_45b4-9j7u/row-i...  row-ir6p-udib~p59j   
18    https://data.cdc.gov/resource/_45b4-9j7u/row-f...  row-f7g4.25fb.8sd2   
19    https://data.cdc.gov/resource/_45b4-9j7u/row-5...  row-52vi_b7p5.27uc   
20    https://data.cdc.gov/resource/_45b4-9j7u/row-b...  row-bkuw.qtg6~rm7n   
21    https://data.cdc.gov/resource/_45b4-9j7u/row-b...  row-bs28-6pbn~i9yn   
22    https://data.cdc.gov/resource/_45b4-9j7u/row-z...  row-z25n-kac7.mwxk   
23    https://data.cdc.gov/resource/_45b4-9j7u/row-7...  row-7v5g~65x8.mzrz   
24    https://data.cdc.gov/resource/_45b4-9j7u/row-k...  row-kqky-zpbq~fpa8   
25    https://data.cdc.gov/resource/_45b4-9j7u/row-2...  row-2qxw_qqj4~tdbf   
26    https://data.cdc.gov/resource/_45b4-9j7u/row-3...  row-3uxb.eff5~2kfk   
27    https://data.cdc.gov/resource/_45b4-9j7u/row-h...  row-htes-wr8u.xjpx   
28    https://data.cdc.gov/resource/_45b4-9j7u/row-j...  row-ju49.edym_g3es   
29    https://data.cdc.gov/resource/_45b4-9j7u/row-n...  row-nums~qyfc.4a36   
...                                                 ...                 ...   
3299  https://data.cdc.gov/resource/_45b4-9j7u/row-s...  row-s52s-ypcp_3cpe   
3300  https://data.cdc.gov/resource/_45b4-9j7u/row-p...  row-pv44_hsps_vt9r   
3301  https://data.cdc.gov/resource/_45b4-9j7u/row-g...  row-gdca_hjct.s6uw   
3302  https://data.cdc.gov/resource/_45b4-9j7u/row-w...  row-w72h_ucxj~y9bg   
3303  https://data.cdc.gov/resource/_45b4-9j7u/row-m...  row-mq5i.48wk-ikgv   
3304  https://data.cdc.gov/resource/_45b4-9j7u/row-u...  row-ukfd_sgz2-ac8j   
3305  https://data.cdc.gov/resource/_45b4-9j7u/row-p...  row-peiq_i83r-ih4a   
3306  https://data.cdc.gov/resource/_45b4-9j7u/row-s...  row-sddt.5wja_k35j   
3307  https://data.cdc.gov/resource/_45b4-9j7u/row-v...  row-vrvm_2dvg.egmu   
3308  https://data.cdc.gov/resource/_45b4-9j7u/row-6...  row-67cm.57sp.n49v   
3309  https://data.cdc.gov/resource/_45b4-9j7u/row-7...  row-7vnd.md8u.i7bq   
3310  https://data.cdc.gov/resource/_45b4-9j7u/row-j...  row-jgen-6kgs-92gh   
3311  https://data.cdc.gov/resource/_45b4-9j7u/row-j...  row-jg2i.byh6_jzi9   
3312  https://data.cdc.gov/resource/_45b4-9j7u/row-f...  row-fcyc.idak.b893   
3313  https://data.cdc.gov/resource/_45b4-9j7u/row-m...  row-mei8~b9vn~iwku   
3314  https://data.cdc.gov/resource/_45b4-9j7u/row-3...  row-3n4a.36g6~fufs   
3315  https://data.cdc.gov/resource/_45b4-9j7u/row-p...  row-pc46_jx5g.hg26   
3316  https://data.cdc.gov/resource/_45b4-9j7u/row-x...  row-xut2~ebaf_b2cn   
3317  https://data.cdc.gov/resource/_45b4-9j7u/row-z...  row-z3dr~9v3c.vp3r   
3318  https://dat

In [34]:
##################################################################################################################
#
# YouDo: 
#  Make a visualization showing week vs cum_2017 for all of the top 5 diseases
#  Ensure it has appropriate labels, etc. for pulblication
fig, ax  = plt.subplots()

# diz is the top 5 diseases we found above
for diz in df.iloc[:5,:].Disease:
    # Pulls all mention of each disease from df2
    this_diz = df2[[xx.startswith(diz) for xx in df2.disease]]
    # sorts the cum_2017 values 
    this_diz.sort_values('cum_2017')
    # Plots each disease (so there are 5 lines)
    plt.plot(this_diz.mmwr_week, [float(xx) for xx in this_diz.cum_2017],label=diz)
plt.legend()
plt.xlabel('Week Number')
plt.ylabel('Cumulative Reports of Disease')
ax.xaxis.set_major_locator(plt.MaxNLocator(15))

<IPython.core.display.Javascript object>

NameError: name 'df' is not defined

In [160]:
df.iloc[:5,:].Disease

15                            Cyclosporiasis**
28                                 Listeriosis
46                     Syphilis, congenital¶¶¶
63    Zika virus disease, non-congenital††††  
45        Streptococcal toxic-shock syndrome**
Name: Disease, dtype: object

In [161]:
df2[[xx.startswith(diz) for xx in df2.disease]]

@_address                @_id  \
45    https://data.cdc.gov/resource/_45b4-9j7u/row-r...  row-rdii-3fwz_sizh   
109   https://data.cdc.gov/resource/_45b4-9j7u/row-q...  row-q3n3-n74h-m4h4   
155   https://data.cdc.gov/resource/_45b4-9j7u/row-a...  row-arnk-vgyx-sngy   
202   https://data.cdc.gov/resource/_45b4-9j7u/row-t...  row-tiys-9fgj.4ww5   
273   https://data.cdc.gov/resource/_45b4-9j7u/row-s...  row-sz9f~uuwv-hc4i   
356   https://data.cdc.gov/resource/_45b4-9j7u/row-q...  row-qa7q.yz8b-54yu   
385   https://data.cdc.gov/resource/_45b4-9j7u/row-6...  row-6732~za3y~3g9s   
460   https://data.cdc.gov/resource/_45b4-9j7u/row-v...  row-vfdq.u4ig-pviw   
549   https://data.cdc.gov/resource/_45b4-9j7u/row-8...  row-838m_6i74-2rzm   
585   https://data.cdc.gov/resource/_45b4-9j7u/row-u...  row-u7zu-z37p.p968   
656   https://data.cdc.gov/resource/_45b4-9j7u/row-q...  row-qwq7_uq8f-fua2   
726   https://data.cdc.gov/resource/_45b4-9j7u/row-c...  row-crmc-k4jm_s8j9   
831   https://data.cdc.gov/resource/_45b4-9j7u/row-v...  row-vu2f~9z78.ygkm   
873   https://data.cdc.gov/resource/_45b4-9j7u/row-6...  row-62sw_ji55~vj8k   
910   https://data.cdc.gov/resource/_45b4-9j7u/row-4...  row-4s39-y5xb.i2gb   
1020  https://data.cdc.gov/resource/_45b4-9j7u/row-m...  row-mggq_8rny.tnpu   
1055  https://data.cdc.gov/resource/_45b4-9j7u/row-a...  row-avbe~gbty~5asb   
1136  https://data.cdc.gov/resource/_45b4-9j7u/row-e...  row-ec93-st3u_yunr   
1213  https://data.cdc.gov/resource/_45b4-9j7u/row-i...  row-iy7c_d5su.bj3e   
1221  https://data.cdc.gov/resource/_45b4-9j7u/row-x...  row-x4de_ewed-s732   
1328  https://data.cdc.gov/resource/_45b4-9j7u/row-4...  row-4kuh~6m47_7j4i   
1348  https://data.cdc.gov/resource/_45b4-9j7u/row-d...  row-df55.5zjv.spa8   
1452  https://data.cdc.gov/resource/_45b4-9j7u/row-c...  row-ckka-7ae8_deky   
1501  https://data.cdc.gov/resource/_45b4-9j7u/row-4...  row-4igt-ec6d~ihtm   
1538  https://data.cdc.gov/resource/_45b4-9j7u/row-r...  row-rse8~nj3k~z4u3   
1652  https://data.cdc.gov/resource/_45b4-9j7u/row-c...  row-cvfk~g4c9_ng9x   
1682  https://data.cdc.gov/resource/_45b4-9j7u/row-k...  row-kpq3.xwnx_s44j   
1769  https://data.cdc.gov/resource/_45b4-9j7u/row-4...  row-4ezc.wh43-ix4q   
1844  https://data.cdc.gov/resource/_45b4-9j7u/row-n...  row-nu5u~vmew~m2ab   
1887  https://data.cdc.gov/resource/_45b4-9j7u/row-3...  row-3sfi-embx_ytzj   
1968  https://data.cdc.gov/resource/_45b4-9j7u/row-v...  row-v27h.uyfi-zsf3   
2007  https://data.cdc.gov/resource/_45b4-9j7u/row-2...  row-2rhg.cp4f.bn7s   
2067  https://data.cdc.gov/resource/_45b4-9j7u/row-h...  row-h5i6_x6pc_jbsr   
2128  https://data.cdc.gov/resource/_45b4-9j7u/row-p...  row-phw3.7p54.rs29   
2186  https://data.cdc.gov/resource/_45b4-9j7u/row-2...  row-2ewi-f95g.aq3a   
2260  https://data.cdc.gov/resource/_45b4-9j7u/row-e...  row-ed6a.rf9x~6f9n   
2310  https://data.cdc.gov/resource/_45b4-9j7u/row-h...  row-hipk.3iiy_nmgx   
2389  https://data.cdc.gov/resource/_45b4-9j7u/row-s...  row-sv84-i928~rzja   
2461  https://data.cdc.gov/resource/_45b4-9j7u/row-2...  row-2x73.99hu-bsdp   
2533  https://data.cdc.gov/resource/_45b4-9j7u/row-4...  row-4hwb_4kre_57wh   
2568  https://data.cdc.gov/resource/_45b4-9j7u/row-f...  row-f49x_rjfd_xt67   
2639  https://data.cdc.gov/resource/_45b4-9j7u/row-r...  row-rqci.g587-qpx7   
2731  https://data.cdc.gov/resource/_45b4-9j7u/row-y...  row-yq28~gx73~zyj5   
2815  https://data.cdc.gov/resource/_45b4-9j7u/row-x...  row-xegb_vnxt~v8nx   
2855  https://data.cdc.gov/resource/_45b4-9j7u/row-t...  row-tswf.kc9u~mnf8   
2905  https://data.cdc.gov/resource/_45b4-9j7u/row-r...  row-rmiz_wg2c.hskv   
3009  https://data.cdc.gov/resource/_45b4-9j7u/row-i...  row-ij3e.weu7-p8mq   
3026  https://data.cdc.gov/resource/_45b4-9j7u/row-g...  row-gifb.njub-pvpr   
3113  https://data.cdc.gov/resource/_45b4-9j7u/row-a...  row-ae8y-wqs3_a4xs   
3185  https://data.cdc.gov/resource/_45b4-9j7u/row-u...  row-ur9u_bkk9~9f8h   
3308  https://dat

In [189]:
[type(xx) for xx in this_diz.cum_2017]

[float,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str,
 str]

In [164]:
rabies.columns

Index(['@_id', '@_uuid', '@_position', '@_address', 'disease', 'mmwr_year',
       'mmwr_week', 'current_week_flag', 'cum_2017_flag',
       '_5_year_weekly_average_flag', 'total_cases_reported_2016_flag',
       'total_cases_reported_2015_flag', 'total_cases_reported_2014_flag',
       'total_cases_reported_2013_flag', 'total_cases_reported_2012_flag',
       '_5_year_weekly_average', 'total_cases_reported_2016',
       'total_cases_reported_2015', 'total_cases_reported_2014',
       'total_cases_reported_2013', 'total_cases_reported_2012',
       'current_week', 'cum_2017',
       'states_reporting_cases_during_current_week_no'],
      dtype='object')